In [ ]:
!pip install transformers

In [ ]:
# @markdown Use the T5 encoder only
# Step 2: Import necessary libraries
from transformers import T5Tokenizer, T5Model
import torch

# Step 3: Load the T5 tokenizer and model
# You can use 't5-small', 't5-base', 't5-large', etc. 't5-small' is lighter for Colab
tokenizer = T5Tokenizer.from_pretrained("t5-base")
model = T5Model.from_pretrained("t5-base")

# Step 4: Define the input string
input_string = "Studies have shown that owning a dog is good for you"   # @param {type:'string'}

# Step 5: Tokenize the input string to get token IDs
input_ids = tokenizer(input_string, return_tensors="pt").input_ids
print("Token IDs:", input_ids)

# Step 6: (Optional) Get hidden state embeddings
# Ensure the model is in evaluation mode
model.eval()

# Forward pass to get encoder outputs
with torch.no_grad():
    outputs = model.encoder(input_ids=input_ids)
    encoder_hidden_states = outputs.last_hidden_state

# Print the shape of the hidden states
print("Encoder Hidden States Shape:", encoder_hidden_states.shape)
# Example: Shape will be [batch_size, sequence_length, hidden_size], e.g., [1, num_tokens, 768] for t5-base

# Step 7: (Optional) Decode token IDs back to text for verification
decoded_text = tokenizer.decode(input_ids[0], skip_special_tokens=True)
print("Decoded Text:", decoded_text)

In [ ]:
# @markdown 🇫🇷 Translate using the T5 model  <br>
# @markdown Note: NOT a FLUX feature since FLUX only uses the T5 encoder!

# Step 2: Import necessary libraries
from transformers import T5Tokenizer, T5ForConditionalGeneration

# Step 3: Load the T5 tokenizer and model
# Use 't5-base' for balance; 't5-small' for speed, or 't5-large' for better performance
tokenizer = T5Tokenizer.from_pretrained("t5-base")
model = T5ForConditionalGeneration.from_pretrained("t5-base")

# Step 4: Define the input string with the instruction
input_string = "translate to French: The sun is shining today." # @param {type:'string'}

# Step 5: Tokenize the input string
input_ids = tokenizer(input_string, return_tensors="pt").input_ids

# Step 6: Generate the output
model.eval()
with torch.no_grad():
    outputs = model.generate(input_ids, max_length=50)
    translated_text = tokenizer.decode(outputs[0], skip_special_tokens=True)

# Step 7: Print the result
print("Translated Text:", translated_text)



In [ ]:
# @markdown ⚖️ Compare Similiarity

# Step 1: Install required libraries
!pip install transformers torch

# Step 2: Import necessary libraries
from transformers import T5Tokenizer, T5Model
import torch
import torch.nn.functional as F

# Step 3: Load T5 tokenizer and model
tokenizer = T5Tokenizer.from_pretrained("t5-base")
model = T5Model.from_pretrained("t5-base")

# Step 4: Define input strings
text1 = "a photo The sun is shining today"  # @param {type:'string'}
text2 = "anime screencap The sun is shining today " # @param {type:'string'}

# Step 5: Tokenize the input strings
inputs1 = tokenizer(text1, return_tensors="pt", padding=True, truncation=True)
inputs2 = tokenizer(text2, return_tensors="pt", padding=True, truncation=True)

# Step 6: Get T5 encoder hidden states
model.eval()
with torch.no_grad():
    # Get encoder outputs for both inputs
    outputs1 = model.encoder(input_ids=inputs1.input_ids)
    outputs2 = model.encoder(input_ids=inputs2.input_ids)

    # Extract last hidden states [batch_size, sequence_length, hidden_size]
    hidden_states1 = outputs1.last_hidden_state
    hidden_states2 = outputs2.last_hidden_state

# Step 7: Aggregate hidden states (mean pooling)
# Average across the sequence dimension to get a single vector per input
embedding1 = hidden_states1.mean(dim=1)  # Shape: [1, hidden_size]
embedding2 = hidden_states2.mean(dim=1)  # Shape: [1, hidden_size]

# Step 8: Compute cosine similarity
cosine_sim = F.cosine_similarity(embedding1, embedding2, dim=1)
print("Cosine Similarity:", cosine_sim.item())

# Step 9: (Optional) Print token IDs for reference
print("Token IDs for text1:", inputs1.input_ids)
print("Token IDs for text2:", inputs2.input_ids)